In [1]:
import numpy as np
import pandas as pd
import h5py
import gc

import sklearn as sk

from sklearn.model_selection import ParameterGrid




import os
    

import tensorflow as tf
from tensorflow.keras import mixed_precision
from tensorflow.keras.utils import GeneratorEnqueuer

os.environ['TF_CPP_MIN_LOG_LEVEL']='2'
os.environ['CUDA_VISIBLE_DEVICES']="0" 

gpus = tf.config.experimental.list_physical_devices('GPU')
if gpus:
  try:
    # Currently, memory growth needs to be the same across GPUs
    for gpu in gpus:
      tf.config.experimental.set_memory_growth(gpu, True)
    logical_gpus = tf.config.experimental.list_logical_devices('GPU')
    print(len(gpus), "Physical GPUs,", len(logical_gpus), "Logical GPUs")
  except RuntimeError as e:
    # Memory growth must be set before GPUs have been initialized
    print(e)


base_dir = '/media/tord/T7/Thesis_ssd/MasterThesis3'
os.chdir(base_dir)

from Classes.Modeling.DynamicModels import DynamicModels
from Classes.Modeling.StaticModels import StaticModels
from Classes.DataProcessing.LoadData import LoadData
from Classes.DataProcessing.HelperFunctions import HelperFunctions
from Classes.DataProcessing.DataHandler import DataHandler
from Classes.Modeling.GridSearchResultProcessor import GridSearchResultProcessor
from Classes.DataProcessing.ts_RamGenerator import data_generator
from Classes.Modeling.TrainSingleModelRamLess import TrainSingleModelRamLess
from Classes.DataProcessing.RamLessLoader import RamLessLoader



import sys


import random
import pprint
import re
import json

1 Physical GPUs, 1 Logical GPUs

INFO:tensorflow:Mixed precision compatibility check (mixed_float16): OK
Your GPU will likely run quickly with dtype policy mixed_float16 as it has compute capability of at least 7.0. Your GPU: GeForce RTX 3090, compute capability 8.6


In [2]:
load_args = {
    'earth_explo_only' : True,
    'noise_earth_only' : False,
    'noise_not_noise' : False,
    'downsample' : True,
    'upsample' : True,
    'frac_diff' : 1,
    'seed' : 1,
    'subsample_size' : 0.25,
    'balance_non_train_set' : False,
    'use_true_test_set' : False,
    'even_balance' : True
}
loadData = LoadData(**load_args)
train_ds, val_ds, test_ds = loadData.get_datasets()
noise_ds = loadData.noise_ds
handler = DataHandler(loadData)
helper = HelperFunctions()

2 2
Mapping train redundancy: : [--------------------------------------->] 100 %

Mapping validation redundancy: : [--------------------------------------->] 100 %

Mapping test redundancy: : [--------------------------------------->] 100 %



Loaded explosion and earthquake dataset:
Evenly balanced among classes in the train set.
Distribution (Label: (counts, proportion)) of
Train ds:
earthquake: (20507, 0.4987)  |  explosion: (20616, 0.5013)  
Val ds:
earthquake: (255, 0.0762)  |  explosion: (3092, 0.9238)  
Test ds:
earthquake: (176, 0.0789)  |  explosion: (2055, 0.9211)  


# TrainSingleModelRamLess Development:

In [3]:
model_type = "DENSE_baseline"
is_lstm = True
num_channels = 3    

use_time_augmentor = True
scaler_name = "standard"
use_noise_augmentor = False
filter_name = None
band_min = 2.0
band_max = 4.0
highpass_freq = 0.075


shutdown = False

num_classes = len(list(set(loadData.label_dict.values())))



ramLessLoader = RamLessLoader(loadData, 
                      handler, 
                      use_time_augmentor = use_time_augmentor, 
                      use_noise_augmentor = use_noise_augmentor, 
                      scaler_name = scaler_name,
                      filter_name = filter_name, 
                      band_min = band_min,
                      band_max = band_max,
                      highpass_freq = highpass_freq, 
                      load_test_set = False, 
                      meier_load = False)

ramLessLoader.fit()

Fitting noise set time augmentor: [--------------------------------------->] 100 %

Fit process completed after 9.972749948501587 seconds. Total datapoints fitted: 21199.
Average time per datapoint: 0.000470434923746478




Fitting train time augmentor: [--------------------------------------->] 100 %

Fit process completed after 13.900656700134277 seconds. Total datapoints fitted: 41123.
Average time per datapoint: 0.0003380263283353422




Fitting validation time augmentor: [--------------------------------------->] 100 %

Fit process completed after 1.6531074047088623 seconds. Total datapoints fitted: 3347.
Average time per datapoint: 0.0004939072018849305






Fitting standard scaler:: [--------------------------------------->] 100 %

Process took 0:01:04.756636 seconds.


In [5]:


use_tensorboard = True
use_liveplots = False
use_custom_callback = True
use_early_stopping = False
start_from_scratch = False
use_reduced_lr = False
log_data = False

beta = 3

def clear_tensorboard_dir():
        import os
        import shutil
        path = f"{base_dir}/Tensorboard_dir/fit"
        files = os.listdir(path)
        print(files)
        for f in files:
            shutil.rmtree(os.path.join(path,f))
if use_tensorboard:
    clear_tensorboard_dir()


modelTrain = TrainSingleModelRamLess(ramLessLoader, helper, loadData, 
                                     model_type, num_channels, use_tensorboard, use_liveplots, 
                                     use_custom_callback, use_early_stopping, use_reduced_lr, 
                                     log_data = True, start_from_scratch = False, beta = beta)
params = {
        "batch_size" : 128,
        "epochs" : 10,
        "learning_rate" : 0.01,
        "optimizer" : "sgd",
        "units" : 50,
        "dense_activation" : "relu",
        "output_layer_activation" : "sigmoid"
    }

model, _ = modelTrain.run(ramLessLoader, 16, 15, evaluate_train = False, evaluate_val = False, **params)

['20210423-201205']
Trying to create result file
Made result file:  results_DENSE_baseline_earthExplo_timeAug_standard_unbalanced_valtest_subsample-0.25_numChannels-3_f3.csv
[   {'model_type': 'DENSE_baseline'},
    {   'batch_size': 128,
        'dense_activation': 'relu',
        'epochs': 10,
        'learning_rate': 0.01,
        'optimizer': 'sgd',
        'output_layer_activation': 'sigmoid',
        'units': 50}]
Saving file. 12 rows.
results_DENSE_baseline_earthExplo_timeAug_standard_unbalanced_valtest_subsample-0.25_numChannels-3_f3.csv saved to path:   /media/tord/T7/Thesis_ssd/MasterThesis3/GridSearchResults/2_classes
Model: "model"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         [(None, 6000, 3)]         0         
_________________________________________________________________
flatten (Flatten)            (None, 18000)             0         
__________________

Traceback (most recent call last):
  File "/media/tord/T7/Thesis_ssd/MasterThesis3/Classes/Modeling/TrainSingleModel.py", line 113, in fit_model
    model.fit(train_enq.get(), **fit_args)
  File "/home/tord/miniconda3/envs/thesis/lib/python3.8/site-packages/tensorflow/python/keras/engine/training.py", line 1134, in fit
    tmp_logs = self.train_function(iterator)
  File "/home/tord/miniconda3/envs/thesis/lib/python3.8/site-packages/tensorflow/python/eager/def_function.py", line 818, in __call__
    result = self._call(*args, **kwds)
  File "/home/tord/miniconda3/envs/thesis/lib/python3.8/site-packages/tensorflow/python/eager/def_function.py", line 846, in _call
    return self._stateless_fn(*args, **kwds)  # pylint: disable=not-callable
  File "/home/tord/miniconda3/envs/thesis/lib/python3.8/site-packages/tensorflow/python/eager/function.py", line 2993, in __call__
    return graph_function._call_flat(
  File "/home/tord/miniconda3/envs/thesis/lib/python3.8/site-packages/tensorflow/pyt

AttributeError: 'NoneType' object has no attribute 'evaluate'

In [ ]:
from Classes.DataProcessing.ts_RamGenerator import ramless_data_generator

In [ ]:
enq = GeneratorEnqueuer(ramless_data_generator(val_ds, ramLessLoader.y_val, 
                                               100, ramLessLoader, 
                                               ramLessLoader.val_timeAug,
                                               3, True, False))
enq.start(workers = 8, max_queue_size = 10)
gen = enq.get()

In [ ]:
x_val = next(gen)[0]

In [ ]:
enq.stop()
del enq, gen

In [ ]:
i = 0

In [ ]:
x_val.shape

In [ ]:
original_trace, sample_info = handler.path_to_trace(val_ds[i][0])
label_text = val_ds[i][1]
print(label_text, ramLessLoader.y_val[i])
pre_aug = np.reshape(x_val[i],(3, 6000))


helper.plot_event(pre_aug, sample_info)
helper.plot_event(original_trace, sample_info)
pp = pprint.PrettyPrinter(indent=4)
pp.pprint(sample_info)
i+=1

In [ ]:
ramLessLoader.y_val

In [ ]:
assert loadData.train.all() == ramLessLoader.train_ds.all()

In [ ]:
loadData.train[0:5], ramLessLoader.train_ds[0:5]